# 2025 NLP Project
This project implements an **automated fact-checking system** designed to verify claims related to climate science. Given a claim, the system retrieves relevant evidence passages from a knowledge source and classifies the claim into one of four categories:
- **SUPPORTS**
- **REFUTES**
- **NOT_ENOUGH_INFO**
- **DISPUTED**

# Readme


# 1.DataSet Processing
(You can add as many code blocks and text blocks as you need. However, YOU SHOULD NOT MODIFY the section title)

In [ ]:
# Install package and dependence
from tqdm import tqdm
import os
import numpy as np
import json
import pandas as pd
import torch
import random
import transformers


import torch.nn.functional as F
import torch.nn as nn
from torch.optim import AdamW
from torch.utils.data import DataLoader
from sentence_transformers import SentenceTransformer, util
from transformers import EarlyStoppingCallback
from transformers import TrainingArguments, Trainer
from torch.nn import TransformerEncoder, TransformerEncoderLayer
from transformers import BertModel, BertConfig, BertTokenizer, BertForSequenceClassification, get_linear_schedule_with_warmup
from transformers import AutoTokenizer, AutoModelForCausalLM, pipeline
from torch.utils.data import Dataset
from collections import defaultdict, Counter

# define device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

#set random seeds
def set_seed(seed):
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False

set_seed(36)

### 1.1 read all data and transform to dataframe

In [ ]:
# read data
with open('train-claims.json', 'r', encoding='utf-8') as file:
    data_train = json.load(file)

with open('dev-claims.json', 'r', encoding='utf-8') as file:
    data_dev = json.load(file)

with open('evidence.json', 'r', encoding='utf-8') as file:
    evidence_dict = json.load(file)

with open('test-claims-unlabelled.json', 'r', encoding='utf-8') as file:
    data_test = json.load(file)


df_train = pd.DataFrame.from_dict(data_train, orient='index').reset_index()
df_train = df_train.rename(columns={'index': 'claim_id'})

df_dev = pd.DataFrame.from_dict(data_dev, orient='index').reset_index()
df_dev = df_dev.rename(columns={'index': 'claim_id'})

df_evidence = pd.DataFrame(list(evidence_dict.items()), columns=['evidence_id', 'evidence_text'])

df_test = pd.DataFrame.from_dict(data_test, orient='index').reset_index()
df_test = df_test.rename(columns={'index': 'claim_id'})

### 1.2 Extract *evidence_ids* and *evidence_texts*

In [ ]:
evidence_ids = list(evidence_dict.keys())
evidence_texts = [evidence_dict[eid] for eid in evidence_ids]
evidence_id_dict = {eid: idx for idx, eid in enumerate(evidence_ids)}  # evidence_id → idx

### 1.3 Embed the evidence into a tensor

In [ ]:
# load Sentence BERT model to pretrain
sbert_model = SentenceTransformer('all-MiniLM-L6-v2')
sbert_model.eval()

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.5k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
)

In [ ]:
# # Encode all evidences into embeddings
evidence_embeddings = sbert_model.encode(evidence_texts, convert_to_tensor=True)

# 2. Evidence Retrival
(You can add as many code blocks and text blocks as you need. However, YOU SHOULD NOT MODIFY the section title)

## 2.1 Model Implementation

### 2.1.1 Baseline use SBERT


In [ ]:
def retrieve_topk_evidences(claim_text, k=5):

    claim_embedding = sbert_model.encode(claim_text, convert_to_tensor=True)
    cosine_scores = util.cos_sim(claim_embedding, evidence_embeddings) # Compute cosine similarity
    topk_indices = torch.topk(cosine_scores, k=k).indices.squeeze(0) # Get the Top-K highest scoring evidence indices
    topk_evidence_ids = [evidence_ids[idx] for idx in topk_indices.tolist()] # Map back to evidence IDs

    return topk_evidence_ids

### 2.1.2 SBERT Reranker with Random Negatives

In [ ]:
claims = data_train

pairs, labels = [], []

for claim_id, c in tqdm(claims.items()):
    claim_text = c['claim_text']
    gold_ids = set(c['evidences'])

    for eid in gold_ids:
        if eid in evidence_dict:
            pairs.append((claim_text, evidence_dict[eid]))
            labels.append(1)

    neg_sampled = random.sample(list(set(evidence_dict.keys()) - gold_ids), len(gold_ids))
    for eid in neg_sampled:
        if eid in evidence_dict:
            pairs.append((claim_text, evidence_dict[eid]))
            labels.append(0)

100%|██████████| 1228/1228 [07:19<00:00,  2.79it/s]


In [ ]:
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

class ClaimEvidenceDataset(Dataset):
    def __init__(self, pairs, labels):
        self.encodings = tokenizer(
            [p[0] for p in pairs],
            [p[1] for p in pairs],
            truncation=True,
            padding=True,
            max_length=256
        )
        self.labels = labels

    def __getitem__(self, idx):
        item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()}
        item["labels"] = torch.tensor(self.labels[idx])
        return item

    def __len__(self):
        return len(self.labels)

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

In [ ]:
dataset = ClaimEvidenceDataset(pairs, labels)
rerank_model = BertForSequenceClassification.from_pretrained('bert-base-uncased', num_labels=2)

training_args = TrainingArguments(
    output_dir="./bert_reranker",
    per_device_train_batch_size=16,
    num_train_epochs=2,
    logging_dir="./logs",
    save_strategy="no",
    report_to="none"
)

trainer = Trainer(
    model=rerank_model,
    args=training_args,
    train_dataset=dataset
)

trainer.train()

Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pai

TrainOutput(global_step=1032, training_loss=0.043244966471842096, metrics={'train_runtime': 164.482, 'train_samples_per_second': 100.242, 'train_steps_per_second': 6.274, 'total_flos': 2169087540387840.0, 'train_loss': 0.043244966471842096, 'epoch': 2.0})

In [ ]:
rerank_model.save_pretrained("./bert_reranker")
tokenizer.save_pretrained("./bert_reranker")

('./bert_reranker/tokenizer_config.json',
 './bert_reranker/special_tokens_map.json',
 './bert_reranker/vocab.txt',
 './bert_reranker/added_tokens.json')

In [ ]:
def rerank_claim_evidences(claim_text, candidate_evidences, model, tokenizer, top_k=5):
    model.eval()
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    model.to(device)

    inputs = tokenizer(
        [claim_text] * len(candidate_evidences),
        candidate_evidences,
        truncation=True,
        padding=True,
        return_tensors="pt"
    )

    inputs = {k: v.to(device) for k, v in inputs.items()}

    with torch.no_grad():
        outputs = model(**inputs)
        probs = torch.softmax(outputs.logits, dim=1)[:, 1]

    scored = list(zip(candidate_evidences, probs.tolist()))
    scored = sorted(scored, key=lambda x: x[1], reverse=True)
    return [e for e, s in scored[:top_k]]

### 2.1.3 SBERT Reranker with Hard Negatives

In [ ]:
train_texts, train_evidences = [], []
for cid, info in data_train.items():
    train_texts.append(info["claim_text"])
    train_evidences.append([evidence_id_dict[eid] for eid in info["evidences"] if eid in evidence_id_dict])

train_pairs, train_labels = [], []
for idx, claim_text in tqdm(enumerate(train_texts), total=len(train_texts)):
    gold_ids = set(train_evidences[idx])
    claim_emb = sbert_model.encode(claim_text, convert_to_tensor=True)
    cos_scores = util.cos_sim(claim_emb, evidence_embeddings)[0]
    top_idx = torch.topk(cos_scores, k=20).indices.tolist()

    for eid in top_idx:
        label = 1 if eid in gold_ids else 0
        train_pairs.append((claim_text, evidence_texts[eid]))
        train_labels.append(label)

100%|██████████| 1228/1228 [00:15<00:00, 79.59it/s]


In [ ]:
tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")

train_dataset = ClaimEvidenceDataset(train_pairs, train_labels)
model = BertForSequenceClassification.from_pretrained("bert-base-uncased", num_labels=2)

Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
learning_rates = [2e-5, 3e-5, 5e-5]

# Grid search
for lr in learning_rates:
    print(f"\n Training with learning_rate = {lr}")
    model_output_dir = f"./bert_reranker_lr{str(lr).replace('.', '')}"

    model = BertForSequenceClassification.from_pretrained("bert-base-uncased", num_labels=2)

    training_args = TrainingArguments(
        output_dir=model_output_dir,
        per_device_train_batch_size=16,
        num_train_epochs=3,
        learning_rate=lr,
        logging_dir=f"{model_output_dir}/logs",
        save_strategy="no",
        report_to="wandb",
        run_name = f"bert_rerank_hard_learning_rate_{lr}",
        logging_steps=500
    )

    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset
    )

    trainer.train()

    model.save_pretrained(model_output_dir)
    tokenizer.save_pretrained(model_output_dir)


 Training with learning_rate = 2e-05


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.



 Training with learning_rate = 3e-05


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.



 Training with learning_rate = 5e-05


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


## 2.2 Evidence Retrival

### 2.1.1 Baseline

#### Evaluation on Develop dataset

In [ ]:
predictions = {}

# Iterate over df_dev with each row corresponding to a claim
for _, row in df_dev.iterrows():
    claim_id = row['claim_id']
    claim_text = row['claim_text']
    claim_label = row['claim_label']

    topk_evidences_id = retrieve_topk_evidences(claim_text, k=5)

    predictions[claim_id] = {
        "claim_text": claim_text,
        "claim_label": claim_label,
        "evidences": topk_evidences_id
    }

with open('dev-claims-predictions-baseline.json', 'w') as f:
  json.dump(predictions, f, indent=2)

In [ ]:
!python eval.py --predictions dev-claims-predictions-baseline.json --groundtruth dev-claims.json

Evidence Retrieval F-score (F)    = 0.14716553287981862
Claim Classification Accuracy (A) = 1.0
Harmonic Mean of F and A          = 0.25657244514726235


#### Prediction on Test dataset

In [ ]:
test_predictions_baseline = {}

for _, row in df_test.iterrows():
    claim_id = row['claim_id']
    claim_text = row['claim_text']

    topk_evidences_id = retrieve_topk_evidences(claim_text, k=5)

    test_predictions_baseline[claim_id] = {
        "claim_text": claim_text,
        "evidences": topk_evidences_id
    }

with open("test-claims-predictions-baseline.json", "w") as f:
    json.dump(test_predictions_baseline, f, indent=2)

### 2.1.2 SBERT Reranker with Random Negatives

#### Evaluation on Develop dataset

In [ ]:
rerank_model = BertForSequenceClassification.from_pretrained("./bert_reranker")
tokenizer = BertTokenizer.from_pretrained("./bert_reranker")

In [ ]:
predictions = {}

for cid, cinfo in tqdm(data_dev.items()):
    claim_text = cinfo["claim_text"]
    true_label = cinfo["claim_label"]

    # Top-20
    candidate_ids = retrieve_topk_evidences(claim_text, k=20)
    candidate_texts = [evidence_dict[eid] for eid in candidate_ids]

    # rerank
    final_texts = rerank_claim_evidences(claim_text, candidate_texts, rerank_model, tokenizer, top_k=5)

    final_ids = []
    for text in final_texts:
        for eid in candidate_ids:
            if evidence_dict[eid] == text and eid not in final_ids:
                final_ids.append(eid)
                break

    predictions[cid] = {
        "claim_text": claim_text,
        "claim_label": true_label,
        "evidences": final_ids
    }

with open("dev-claims-predictionss-rerank.json", "w") as f:
    json.dump(predictions, f, indent=2)

100%|██████████| 154/154 [00:09<00:00, 16.17it/s]


In [ ]:
!python eval.py --predictions dev-claims-predictionss-rerank.json --groundtruth dev-claims.json

Evidence Retrieval F-score (F)    = 0.1580138115852402
Claim Classification Accuracy (A) = 1.0
Harmonic Mean of F and A          = 0.2729048824882845


#### Prediction on Test dataset

In [ ]:
test_predictions = {}

for cid, cinfo in tqdm(data_test.items()):
    claim_text = cinfo["claim_text"]

    # Top-20
    candidate_ids = retrieve_topk_evidences(claim_text, k=20)
    candidate_texts = [evidence_dict[eid] for eid in candidate_ids]

    # rerank
    final_texts = rerank_claim_evidences(claim_text, candidate_texts, rerank_model, tokenizer, top_k=5)

    # find corresponding evidence ID
    final_ids = []
    for text in final_texts:
        for eid in candidate_ids:
            if evidence_dict[eid] == text and eid not in final_ids:
                final_ids.append(eid)
                break

    test_predictions[cid] = {
        "claim_text": claim_text,
        "evidences": final_ids
    }

with open("test-claims-predictions-rerank.json", "w") as f:
    json.dump(test_predictions, f, indent=2)

100%|██████████| 153/153 [00:09<00:00, 16.59it/s]


### 2.1.3 SBERT Reranker with Hard Negatives

#### Evaluation on Develop dataset

In [ ]:
for lr in learning_rates:
    model_dir = f"./bert_reranker_lr{str(lr).replace('.', '')}"
    print(f"Evaluating model: {model_dir}")

    model = BertForSequenceClassification.from_pretrained(model_dir)
    tokenizer = BertTokenizer.from_pretrained(model_dir)
    model.eval()
    model.to("cuda" if torch.cuda.is_available() else "cpu")

    predictions = {}
    for cid, info in tqdm(data_dev.items()):
        claim_text = info["claim_text"]
        true_label = info["claim_label"]

        candidate_ids = retrieve_topk_evidences(claim_text, k=20)
        candidate_texts = [evidence_dict[eid] for eid in candidate_ids]

        reranked_texts = rerank_claim_evidences(claim_text, candidate_texts, model, tokenizer, top_k=5)

        final_ids = []
        for text in reranked_texts:
            for eid in candidate_ids:
                if evidence_dict[eid] == text and eid not in final_ids:
                    final_ids.append(eid)
                    break

        predictions[cid] = {
            "claim_text": claim_text,
            "claim_label": true_label,
            "evidences": final_ids
        }

    pred_file = f"dev-claims-predictions-lr{str(lr).replace('.', '')}.json"
    with open(pred_file, "w") as f:
        json.dump(predictions, f, indent=2)

    os.system(f"python eval.py --predictions {pred_file} --groundtruth dev-claims.json")

    print("===" * 20)


In [ ]:
!python eval.py --predictions dev-claims-predictions-lr2e-05.json --groundtruth dev-claims.json

Evidence Retrieval F-score (F)    = 0.16515666872809728
Claim Classification Accuracy (A) = 1.0
Harmonic Mean of F and A          = 0.2834926377898773


In [ ]:
!python eval.py --predictions dev-claims-predictions-lr3e-05.json --groundtruth dev-claims.json

Evidence Retrieval F-score (F)    = 0.18176664605236034
Claim Classification Accuracy (A) = 1.0
Harmonic Mean of F and A          = 0.30761850769700405


In [ ]:
!python eval.py --predictions dev-claims-predictions-lr5e-05.json --groundtruth dev-claims.json

Evidence Retrieval F-score (F)    = 0.17023809523809524
Claim Classification Accuracy (A) = 1.0
Harmonic Mean of F and A          = 0.29094608341810785


#### Prediction on Test dataset

In [ ]:
best_model = BertForSequenceClassification.from_pretrained("./bert_reranker_lr3e-05")
best_tokenizer = BertTokenizer.from_pretrained("./bert_reranker_lr3e-05")

test_predictions = {}

for cid, cinfo in tqdm(data_test.items(), desc="Predicting test"):
    claim_text = cinfo["claim_text"]

    # Top-20 Sentence-BERT
    candidate_ids = retrieve_topk_evidences(claim_text, k=20)
    candidate_texts = [evidence_dict[eid] for eid in candidate_ids]

    # Rerank
    final_texts = rerank_claim_evidences(claim_text, candidate_texts, best_model, best_tokenizer, top_k=5)

    final_ids = []
    for text in final_texts:
        for eid in candidate_ids:
            if evidence_dict[eid] == text and eid not in final_ids:
                final_ids.append(eid)
                break

    test_predictions[cid] = {
        "claim_text": claim_text,
        "evidences": final_ids
    }

with open("test-claims-predictions-hard.json", "w") as f:
    json.dump(test_predictions, f, indent=2)

Predicting test: 100%|██████████| 153/153 [00:15<00:00, 10.07it/s]


# 3. Classification

## 3.1 Fine-tuned Transformer Models

### 3.1.1 Seperate Evidence + Voting

#### (1) Model Setup & Fine Tuning

In [ ]:
def build_input_pairs(df_claims, df_evidence):
    evid_dict = dict(zip(df_evidence['evidence_id'], df_evidence['evidence_text']))
    pairs = []

    for _, row in df_claims.iterrows():
        claim_id = row['claim_id']
        claim = row['claim_text']
        label = row['claim_label']
        evidence_ids = row['evidences']

        for eid in evidence_ids:
            if eid in evid_dict:
                evidence = evid_dict[eid]
                pairs.append({
                    'claim_id': claim_id,
                    'claim_text': claim,
                    'evidence_id': eid,
                    'evidence_text': evidence,
                    'label': label
                })

    return pd.DataFrame(pairs)


df_train_pairs = build_input_pairs(df_train, df_evidence)
df_dev_pairs = build_input_pairs(df_dev, df_evidence)

label2id = {
    "SUPPORTS": 0,
    "REFUTES": 1,
    "NOT_ENOUGH_INFO": 2,
    "DISPUTED": 3
}
id2label = {v: k for k, v in label2id.items()}

df_train_pairs['label_id'] = df_train_pairs['label'].map(label2id)
df_dev_pairs['label_id'] = df_dev_pairs['label'].map(label2id)

display(df_train_pairs.head(3))

claim_id                                         claim_text  \
0  claim-1937  Not only is there no scientific evidence that ...   
1  claim-1937  Not only is there no scientific evidence that ...   
2  claim-1937  Not only is there no scientific evidence that ...   

        evidence_id                                      evidence_text  \
0   evidence-442946  At very high concentrations (100 times atmosph...   
1  evidence-1194317  Plants can grow as much as 50 percent faster i...   
2    evidence-12171  Higher carbon dioxide concentrations will favo...   

      label  label_id  
0  DISPUTED         3  
1  DISPUTED         3  
2  DISPUTED         3

In [ ]:
class FactCheckDataset(Dataset):
    def __init__(self, df, tokenizer, max_length=512):
        self.df = df
        self.tokenizer = tokenizer
        self.max_length = max_length

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        row = self.df.iloc[idx]
        encoding = self.tokenizer(
            row['claim_text'],
            row['evidence_text'],
            padding='max_length',
            truncation=True,
            max_length=self.max_length,
            return_tensors='pt'
        )
        return {
            'input_ids': encoding['input_ids'].squeeze(0),
            'attention_mask': encoding['attention_mask'].squeeze(0),
            'label': int(row['label_id']),
            'claim_id': row['claim_id']
        }

In [ ]:
def train_epoch(model, loader, optimizer, scheduler, device):
    model.train()
    total_loss = 0
    for batch in tqdm(loader, desc="Training"):
        optimizer.zero_grad()
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)
        labels = batch['label'].to(device)
        outputs = model(input_ids, attention_mask, labels)
        loss = outputs['loss']
        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)
        optimizer.step()
        scheduler.step()
        total_loss += loss.item()
    return total_loss / len(loader)


def evaluate_with_majority_vote(model, loader, device):
    model.eval()
    preds_by_claim = defaultdict(list)
    true_labels_by_claim = {}
    total_loss = 0
    total_samples = 0

    with torch.no_grad():
        for batch in tqdm(loader, desc="Evaluating (with majority vote)"):
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_mask'].to(device)
            labels = batch['label'].to(device)
            claim_ids = batch['claim_id']

            outputs = model(input_ids, attention_mask, labels)
            loss = outputs['loss']
            logits = outputs['logits']
            predictions = torch.argmax(logits, dim=1).cpu().tolist()
            labels = labels.cpu().tolist()

            total_loss += loss.item()
            total_samples += 1

            for cid, pred, label in zip(claim_ids, predictions, labels):
                preds_by_claim[cid].append(pred)
                if cid not in true_labels_by_claim:
                    true_labels_by_claim[cid] = label

    # majority voting
    final_preds = {
        cid: Counter(votes).most_common(1)[0][0]
        for cid, votes in preds_by_claim.items()
    }

    correct = sum(1 for cid in final_preds if final_preds[cid] == true_labels_by_claim[cid])
    accuracy = correct / len(final_preds)

    return {
        'loss': total_loss / total_samples,
        'accuracy': accuracy
    }

In [ ]:
bert_tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

with open('dev-claims-predictions-lr3e-05.json', 'r', encoding='utf-8') as file:
    data_dev = json.load(file)

df_dev = pd.DataFrame.from_dict(data_dev, orient='index').reset_index().rename(columns={'index': 'claim_id'})
df_dev_pairs = build_input_pairs(df_dev, df_evidence)
df_dev_pairs['label_id'] = df_dev_pairs['label'].map(label2id)

train_dataset = FactCheckDataset(df_train_pairs, bert_tokenizer, max_length=512)
dev_dataset = FactCheckDataset(df_dev_pairs, bert_tokenizer, max_length=512)

train_loader = DataLoader(train_dataset, batch_size=16, shuffle=True)
dev_loader = DataLoader(dev_dataset, batch_size=16)

In [ ]:
class BertWithCustomTransformer(nn.Module):
    def __init__(
        self,
        num_labels=4,
        bert_model="bert-base-uncased",
        hidden_size=768,
        num_heads=8,
        num_layers=2,
        dropout=0.1,
    ):
        super().__init__()

        self.bert = BertModel.from_pretrained(bert_model)
        for param in self.bert.parameters():
            param.requires_grad = False

        encoder_layer = TransformerEncoderLayer(
            d_model=hidden_size,
            nhead=num_heads,
            dim_feedforward=hidden_size * 4,
            dropout=dropout,
            batch_first=True,
        )
        self.custom_transformer = TransformerEncoder(encoder_layer, num_layers=num_layers)

        self.norm = nn.LayerNorm(hidden_size)

        self.classifier = nn.Sequential(
            nn.Dropout(0.2),
            nn.Linear(hidden_size, 256),
            nn.ReLU(),
            nn.Dropout(0.2),
            nn.Linear(256, num_labels)
        )

    def forward(self, input_ids, attention_mask, labels=None):
        outputs = self.bert(
            input_ids=input_ids,
            attention_mask=attention_mask,
            output_hidden_states=False
        )
        bert_output = outputs.last_hidden_state
        transformer_output = self.custom_transformer(bert_output)
        cls_output = transformer_output[:, 0, :]
        logits = self.classifier(self.norm(cls_output))

        if labels is not None:
            loss_fn = nn.CrossEntropyLoss()
            loss = loss_fn(logits, labels)
            return {"loss": loss, "logits": logits}
        return {"logits": logits}

In [ ]:
# do not run -  Training Part
model = BertWithCustomTransformer(
    num_labels=4,
    hidden_size=768,
    num_heads=8,
    num_layers=2,
    dropout=0.1
).to(device)

batch_size = 16
epochs = 5

optimizer = AdamW(model.parameters(), lr=5e-5, eps=1e-8)
total_steps = len(train_loader) * epochs
scheduler = get_linear_schedule_with_warmup(
    optimizer, num_warmup_steps=0, num_training_steps=total_steps
)

for epoch in range(epochs):
    print(f"\n[Transformer] Epoch {epoch+1}/{epochs}")
    train_loss = train_epoch(model, train_loader, optimizer, scheduler, device)
    eval_metrics = evaluate_with_majority_vote(model, dev_loader, device)
    print(f"[Transformer] Train Loss: {train_loss:.4f} | Val Loss: {eval_metrics['loss']:.4f} | Val Acc: {eval_metrics['accuracy']:.4f}")

torch.save(model.state_dict(), "model_bert.pt")


[Transformer] Epoch 1/5


Evaluating (with majority vote): 100%|██████████| 49/49 [00:03<00:00, 14.26it/s]


[Transformer] Train Loss: 1.1432 | Val Loss: 1.2539 | Val Acc: 0.4545

[Transformer] Epoch 2/5


Evaluating (with majority vote): 100%|██████████| 49/49 [00:03<00:00, 14.32it/s]


[Transformer] Train Loss: 1.0565 | Val Loss: 1.2504 | Val Acc: 0.4221

[Transformer] Epoch 3/5


...

[Transformer] Train Loss: 0.9839 | Val Loss: 1.2954 | Val Acc: 0.4416

[Transformer] Epoch 4/5


Evaluating (with majority vote): 100%|██████████| 49/49 [00:03<00:00, 14.29it/s]


[Transformer] Train Loss: 0.9089 | Val Loss: 1.3077 | Val Acc: 0.4805

[Transformer] Epoch 5/5


Evaluating (with majority vote): 100%|██████████| 49/49 [00:03<00:00, 14.11it/s]


[Transformer] Train Loss: 0.8544 | Val Loss: 1.3268 | Val Acc: 0.4675


In [ ]:
model = BertWithCustomTransformer(
    num_labels=4,
    hidden_size=768,
    num_heads=8,
    num_layers=2,
    dropout=0.1
).to(device)

model.load_state_dict(torch.load("model_bert.pt"))
model.to(device)
metrics_bert = evaluate_with_majority_vote(model, dev_loader, device)
print(f"[Transformer] Dev Accuracy: {metrics_bert['accuracy']:.4f}")

/tmp/ipykernel_4625/3709170006.py:9: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  model.load_state_dict(torch.load("model_bert.pt"))
Evaluating (with majority vote): 100%|█

[Transformer] Dev Accuracy: 0.4675


#### (2) Test Inference

In [ ]:
with open("test-claims-predictions-hard.json", "r", encoding='utf-8') as f:
    test_data = json.load(f)

df_test = pd.DataFrame.from_dict(test_data, orient='index').reset_index().rename(columns={'index': 'claim_id'})
df_test['claim_label'] = "SUPPORTS"


df_pairs_test = build_input_pairs(df_test, df_evidence)
df_pairs_test['label_id'] = df_pairs_test['label'].map(label2id)

bert_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
test_dataset = FactCheckDataset(df_pairs_test, bert_tokenizer, max_length=512)
test_loader = DataLoader(test_dataset, batch_size=16, shuffle=False)

model = BertWithCustomTransformer(
    num_labels=4,
    hidden_size=768,
    num_heads=8,
    num_layers=2,
    dropout=0.1
).to(device)

model.load_state_dict(torch.load("model_bert.pt", map_location=device))
model.eval()

claim_preds = defaultdict(list)

with torch.no_grad():
    for batch in tqdm(test_loader, desc="Predicting"):
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)
        claim_ids = batch['claim_id']

        outputs = model(input_ids, attention_mask, labels=None)
        logits = outputs['logits']
        preds = torch.argmax(logits, dim=1).cpu().tolist()

        for cid, pred in zip(claim_ids, preds):
            claim_preds[cid].append(pred)

final_predictions = {}
for cid, votes in claim_preds.items():
    vote_count = Counter(votes)
    final_label_id = vote_count.most_common(1)[0][0]
    final_predictions[cid] = id2label[final_label_id]

for cid, predicted_label in final_predictions.items():
    if cid in test_data:
        test_data[cid]["claim_label"] = predicted_label


with open('test-output-bert.json', 'w', encoding='utf-8') as f:
    json.dump(test_data, f, indent=2, ensure_ascii=False)


/tmp/ipykernel_4625/2284644519.py:24: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  model.load_state_dict(torch.load("model_bert.pt", map_location=device))
Predicting: 100%|

### 3.1.2 Combined Evidences

#### (1) Model Setup & Training

In [ ]:
def build_input_pairs_combined(df_claims, df_evidence, label2id=None, keep_ids=False):
    evid_dict = dict(zip(df_evidence['evidence_id'], df_evidence['evidence_text']))
    pairs = []

    for _, row in df_claims.iterrows():
        claim_id = row['claim_id']
        claim = row['claim_text']
        label = row.get('claim_label')
        evidence_ids = row['evidences']
        evidences = [evid_dict[eid] for eid in evidence_ids if eid in evid_dict]
        combined_evidence = ' [SEP] '.join(evidences)

        pair = {
            'claim_id': claim_id,
            'claim_text': claim,
            'evidence_text': combined_evidence
        }

        if keep_ids:
            pair['evidence_ids'] = evidence_ids

        if label2id and label:
            pair['label'] = label
            pair['label_id'] = label2id[label]

        pairs.append(pair)

    return pd.DataFrame(pairs)

In [ ]:
class FactCheckDataset(Dataset):
    def __init__(self, df, tokenizer, max_length=256):
        self.df = df
        self.tokenizer = tokenizer
        self.max_length = max_length

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        row = self.df.iloc[idx]
        encoding = self.tokenizer(
            row['claim_text'],
            row['evidence_text'],
            padding='max_length',
            truncation=True,
            max_length=self.max_length,
            return_tensors='pt'
        )
        return {
            'input_ids': encoding['input_ids'].squeeze(0),
            'attention_mask': encoding['attention_mask'].squeeze(0),
            'label': int(row['label_id'])
        }

In [ ]:
def train_epoch(model, loader, optimizer, scheduler, device):
    model.train()
    total_loss = 0
    for batch in tqdm(loader, desc="Training"):
        optimizer.zero_grad()
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)
        labels = batch['label'].to(device)
        outputs = model(input_ids, attention_mask, labels)
        loss = outputs['loss']
        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)
        optimizer.step()
        scheduler.step()
        total_loss += loss.item()
    return total_loss / len(loader)

In [ ]:
def evaluate(model, loader, device):
    model.eval()
    total_loss = 0
    correct = 0
    total = 0

    with torch.no_grad():
        for batch in tqdm(loader, desc="Evaluating"):
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_mask'].to(device)
            labels = batch['label'].to(device)

            outputs = model(input_ids, attention_mask, labels)
            loss = outputs['loss']
            logits = outputs['logits']

            total_loss += loss.item()
            preds = torch.argmax(logits, dim=1)
            correct += (preds == labels).sum().item()
            total += labels.size(0)

    return {
        'loss': total_loss / len(loader),
        'accuracy': correct / total
    }



In [ ]:
label2id = {"SUPPORTS": 0, "REFUTES": 1, "NOT_ENOUGH_INFO": 2, "DISPUTED": 3}
bert_tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")

df_train_pairs_combiend = build_input_pairs_combined(df_train, df_evidence, label2id=label2id)
df_dev_pairs_combiend = build_input_pairs_combined(df_dev, df_evidence, label2id=label2id)

train_dataset_combined = FactCheckDataset(df_train_pairs_combiend, bert_tokenizer, max_length=512)
dev_dataset_combined = FactCheckDataset(df_dev_pairs_combiend, bert_tokenizer, max_length=512)

train_loader_combined = DataLoader(train_dataset_combined, batch_size=16, shuffle=True)
dev_loader_combined = DataLoader(dev_dataset_combined, batch_size=16)


In [ ]:
# do not run -  Training Part
model_combined = BertWithCustomTransformer(
    num_labels=4,
    hidden_size=768,
    num_heads=8,
    num_layers=1,
    dropout=0.1
).to(device)

batch_size = 16
epochs = 5

optimizer = AdamW(model_combined.parameters(), lr=6e-6, eps=1e-8)
total_steps = len(train_loader_combined) * epochs
scheduler = get_linear_schedule_with_warmup(
    optimizer, num_warmup_steps=0, num_training_steps=total_steps
)

for epoch in range(5):
    print(f"\n[Transformer Combined] Epoch {epoch+1}/{epochs}")
    train_loss = train_epoch(model_combined, train_loader_combined, optimizer, scheduler, device)
    val_metrics = evaluate(model_combined, dev_loader_combined, device)
    print(f"[Transformer Combined] Train Loss: {train_loss:.4f} | Val Loss: {val_metrics['loss']:.4f} | Val Acc: {val_metrics['accuracy']:.4f}")

torch.save(model_combined.state_dict(), "model_bert_combined.pt")


[Transformer Combined] Epoch 1/5


Evaluating: 100%|██████████| 10/10 [00:00<00:00, 11.76it/s]


[Transformer Combined] Train Loss: 1.3087 | Val Loss: 1.2695 | Val Acc: 0.4740

[Transformer Combined] Epoch 2/5


Evaluating: 100%|██████████| 10/10 [00:00<00:00, 11.47it/s]


[Transformer Combined] Train Loss: 1.2371 | Val Loss: 1.2697 | Val Acc: 0.4870

[Transformer Combined] Epoch 3/5


...

[Transformer Combined] Train Loss: 1.2190 | Val Loss: 1.2673 | Val Acc: 0.4675

[Transformer Combined] Epoch 4/5


Evaluating: 100%|██████████| 10/10 [00:00<00:00, 11.71it/s]


[Transformer Combined] Train Loss: 1.2227 | Val Loss: 1.2667 | Val Acc: 0.4675

[Transformer Combined] Epoch 5/5


Evaluating: 100%|██████████| 10/10 [00:00<00:00, 11.66it/s]


[Transformer Combined] Train Loss: 1.2184 | Val Loss: 1.2659 | Val Acc: 0.4675


In [ ]:
model_combined = BertWithCustomTransformer(
    num_labels=4,
    hidden_size=768,
    num_heads=8,
    num_layers=1,
    dropout=0.1
).to(device)

model_combined.load_state_dict(torch.load("model_bert_combined.pt", map_location=device))
metrics_bert = evaluate(model_combined, dev_loader_combined, device)
print(f"[Transformer Combined] Dev Accuracy: {metrics_bert['accuracy']:.4f}")

/tmp/ipykernel_4625/4179347602.py:9: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  model_combined.load_state_dict(torch.load("model_bert_combined.pt", map_location=device))


[Transformer Combined] Dev Accuracy: 0.4675


#### (2) Test Inference

In [ ]:
# Construct the output dictionary
def generate_prediction_output(df_dev_with_preds, model_name="bert_classifier_combined"):
    output = {}
    for _, row in df_dev_with_preds.iterrows():
        output[row["claim_id"]] = {
            "claim_text": row["claim_text"],
            "claim_label": row["predicted_label"],
            "evidences": row["evidence_ids"]
        }
    return output

In [ ]:
with open("test-claims-predictions-hard.json", "r", encoding='utf-8') as f:
    test_data = json.load(f)

df_test = pd.DataFrame.from_dict(test_data, orient='index').reset_index().rename(columns={'index': 'claim_id'})
df_test["claim_label"] = "SUPPORTS" # fake label

df_pairs_test_combined = build_input_pairs_combined(df_test, df_evidence, label2id=label2id, keep_ids=True)

class TestDataset(Dataset):
    def __init__(self, df, tokenizer, max_length=512):
        self.df = df
        self.tokenizer = tokenizer
        self.max_length = max_length

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        row = self.df.iloc[idx]
        encoding = self.tokenizer(
            row["claim_text"],
            row["evidence_text"],
            padding='max_length',
            truncation=True,
            max_length=self.max_length,
            return_tensors='pt'
        )
        return {
            'input_ids': encoding['input_ids'].squeeze(0),
            'attention_mask': encoding['attention_mask'].squeeze(0),
            'claim_id': row["claim_id"],
            'evidence_ids': row["evidence_ids"]
        }


tokenizer_bert = BertTokenizer.from_pretrained("bert-base-uncased")
test_dataset = TestDataset(df_pairs_test_combined, tokenizer_bert)
test_loader = DataLoader(test_dataset, batch_size=16, shuffle=False)


model_combined = BertWithCustomTransformer(
    num_labels=4,
    hidden_size=768,
    num_heads=8,
    num_layers=1,
    dropout=0.1
).to(device)

model_combined.load_state_dict(torch.load("model_bert_combined.pt", map_location=device))
model_combined.eval()

predictions = []
claim_ids = []
evidence_id_lists = []

with torch.no_grad():
    for batch in test_loader:
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)

        outputs = model(input_ids, attention_mask)
        logits = outputs['logits']
        preds = torch.argmax(logits, dim=1).cpu().tolist()

        predictions.extend(preds)
        claim_ids.extend(batch['claim_id'])
        evidence_id_lists.extend(batch['evidence_ids'])

df_pairs_test_combined["predicted_label"] = [id2label[i] for i in predictions]
output_dict = generate_prediction_output(df_pairs_test_combined, model_name="bert_combined")

with open("test-output-bert-combined.json", "w", encoding="utf-8") as f:
    json.dump(output_dict, f, indent=2, ensure_ascii=False)

/tmp/ipykernel_4625/619079388.py:56: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  model_combined.load_state_dict(torch.load("model_bert_combined.pt", map_location=device))


## 3.2 In-Conext Learning

### 3.2.1 Model Setup

In [ ]:
with open('dev-claims-predictions-lr3e-05.json', 'r', encoding='utf-8') as file:
    data_dev = json.load(file)

df_dev = pd.DataFrame.from_dict(data_dev, orient='index').reset_index()
df_dev = df_dev.rename(columns={'index': 'claim_id'})

In [ ]:
embed_model = SentenceTransformer('all-MiniLM-L6-v2').to(device)

model_name = "distilgpt2"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name).to(device)
generator = pipeline("text-generation", model=model,
    tokenizer=tokenizer,
    device=device
)

Device set to use cuda


In [ ]:
def build_input_pairs_combined(df_claims, df_evidence, label2id=None, keep_ids=False):
    evid_dict = dict(zip(df_evidence['evidence_id'], df_evidence['evidence_text']))
    pairs = []

    for _, row in df_claims.iterrows():
        claim_id = row['claim_id']
        claim = row['claim_text']
        label = row.get('claim_label')
        evidence_ids = row['evidences']

        evidences = [evid_dict[eid] for eid in evidence_ids if eid in evid_dict]

        combined_evidence = '\n'.join([f"Evidence {i+1}: {ev}" for i, ev in enumerate(evidences)])

        pair = {
            'claim_id': claim_id,
            'claim_text': claim,
            'evidence_text': combined_evidence
        }

        if keep_ids:
            pair['evidence_ids'] = evidence_ids

        if label2id and label:
            pair['label'] = label
            pair['label_id'] = label2id[label]

        pairs.append(pair)

    return pd.DataFrame(pairs)


In [ ]:
label2id = {
    "SUPPORTS": 0,
    "REFUTES": 1,
    "NOT_ENOUGH_INFO": 2,
    "DISPUTED": 3
}
id2label = {v: k for k, v in label2id.items()}
df_train_pairs = build_input_pairs_combined(df_train,df_evidence,label2id=label2id)
df_dev_pairs = build_input_pairs_combined(df_dev, df_evidence, label2id=label2id)
train_embeddings = embed_model.encode(df_train_pairs['claim_text'].tolist(), convert_to_tensor=True)

In [ ]:
def get_topk_similar_examples(claim_text, df_train_pairs, train_embeddings, k=5):
    claim_embedding = embed_model.encode(claim_text, convert_to_tensor=True)
    cos_scores = util.pytorch_cos_sim(claim_embedding, train_embeddings)[0]
    topk = torch.topk(cos_scores, k)
    return df_train_pairs.iloc[topk.indices.cpu()]

In [ ]:
def icl_predict_label(claim_text, evidence_text, df_train_pairs, train_embeddings, tokenizer, get_prompt_fn, num_examples=5):
    prompt = get_prompt_fn(
        test_claim_text=claim_text,
        test_evidence_text=evidence_text,
        df_train_pairs=df_train_pairs,
        train_embeddings=train_embeddings,
        tokenizer=tokenizer,
        num_examples=num_examples
    )
    print(prompt)
    output = generator(
        prompt,
        max_new_tokens=10,
        do_sample=False,
        temperature=0.0
    )

    generated_text = output[0]['generated_text']
    answer_part = generated_text.split("Answer:")[-1].strip()

    if not answer_part:
        return "NOT_ENOUGH_INFO"

    answer = answer_part.split()[0].upper()
    return answer


### 3.2.2 Prompt Engineering

#### a. Prompt 1

In [ ]:
def get_prompt1(test_claim_text, test_evidence_text, df_train_pairs, train_embeddings, tokenizer,
                             num_examples=5, max_total_tokens=1000):
    final_block = f"Claim: {test_claim_text}\n{test_evidence_text}\nAnswer (Please answer SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTED):\n"

    prompt = ""
    total_tokens = len(tokenizer(final_block)["input_ids"])

    topk_df = get_topk_similar_examples(test_claim_text, df_train_pairs, train_embeddings, k=30)

    added = 0
    for _, row in topk_df.iterrows():
        example = f"Claim: {row['claim_text']}\n{row['evidence_text']}\nAnswer: {row['label']}\n\n"
        tokens = len(tokenizer(example)["input_ids"])
        if total_tokens + tokens <= max_total_tokens:
            prompt += example
            total_tokens += tokens
            added += 1
        if added >= num_examples:
            break

    prompt += final_block
    return prompt


#### b. Prompt 2

In [ ]:
def get_prompt2(test_claim_text, test_evidence_text, df_train_pairs, train_embeddings, tokenizer,
                             num_examples=5, max_total_tokens=1000):
    definition_block = (
        "Given a claim and supporting evidence, classify the final claim into one of:SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTED"
    )

    final_block = f"Claim: {test_claim_text}\n{test_evidence_text}\nAnswer:"

    prompt = definition_block
    total_tokens = len(tokenizer(definition_block + final_block)["input_ids"])

    topk_df = get_topk_similar_examples(test_claim_text, df_train_pairs, train_embeddings, k=30)

    added = 0
    for _, row in topk_df.iterrows():
        example = f"Claim: {row['claim_text']}\n{row['evidence_text']}\nAnswer: {row['label']}\n\n"
        tokens = len(tokenizer(example)["input_ids"])
        if total_tokens + tokens <= max_total_tokens:
            prompt += example
            total_tokens += tokens
            added += 1
        if added >= num_examples:
            break

    prompt += final_block
    return prompt


#### c. Prompt 3


In [ ]:
def get_prompt3(test_claim_text, test_evidence_text, df_train_pairs, train_embeddings, tokenizer,
                             num_examples=5, max_total_tokens=1000):
    definition_block = (
        "Question: Is the claim supported by the evidence? Answer with one of: SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTED"
    )

    final_block = f"Claim: {test_claim_text}\n{test_evidence_text}\nAnswer:"

    prompt = definition_block
    total_tokens = len(tokenizer(definition_block + final_block)["input_ids"])

    topk_df = get_topk_similar_examples(test_claim_text, df_train_pairs, train_embeddings, k=30)

    added = 0
    for _, row in topk_df.iterrows():
        example = f"Claim: {row['claim_text']}\n{row['evidence_text']}\nAnswer: {row['label']}\n\n"
        tokens = len(tokenizer(example)["input_ids"])
        if total_tokens + tokens <= max_total_tokens:
            prompt += example
            total_tokens += tokens
            added += 1
        if added >= num_examples:
            break

    prompt += final_block
    return prompt


### 3.2.3 Evaluation and Testing

#### a. Prompt 1 Testing


In [ ]:
predicted_1 = []

for _, row in df_dev_pairs.iterrows():
    pred_label_1 = icl_predict_label(
        claim_text=row['claim_text'],
        evidence_text=row['evidence_text'],
        df_train_pairs=df_train_pairs,
        train_embeddings=train_embeddings,
        tokenizer=tokenizer,
        get_prompt_fn=get_prompt1,
        num_examples=5
    )
    predicted_1.append({
        "claim_id": row['claim_id'],
        "claim_text": row['claim_text'],
        "predicted_label": pred_label_1
    })

/usr/local/lib/python3.11/dist-packages/transformers/generation/configuration_utils.py:631: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.0` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Claim: When South Australians buy electricity at $14,200/MWh, they are paying the equivalent of $400 a litre for petrol.
Evidence 1: The retail price of petrol is 75.00 Rs/litre in 2012-13.
Evidence 2: The affordable electricity retail price (860 kcal/kWh at 75% input electricity to shaft power efficiency) to replace petrol (lower heating value 7693 kcal/litre at 33% fuel energy to crank shaft efficiency) is 19.06 Rs/kWh.
Evidence 3: The kilowatt-hour (kWh, also kW⋅h or kW h) is a unit of energy equal to 3600 kilojoules (3.6 megajoules).
Evidence 4: The maximum price was $14,000/MWh in 2016-2017, $13,800/MWh in 2015-2016, $13,500/MWh in 2014-2015, and $13,100/MWh in 2013-2014.
Evidence 5: As of 2018, the unsubsidised levelised cost of electricity for utility scale solar power is around $43/MWh.
Answer: NOT_ENOUGH_INFO

Claim: Australia has more solar coverage than any other continent.
Evidence 1: Australia is the driest inhabited continent; its annual rainfall averaged over continental

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Claim: Fifty-five thousand years ago the whole world was 2°C warmer than it is today[...]
Evidence 1: During the LGM 22,000 YBP the average summer temperature was 3–5 °C (5–9 °F) degrees cooler than today, with variations of 2.9 °C (5.2 °F) degrees cooler on the Seward Peninsula to 7.5 °C (13.5 °F) cooler in the Yukon.
Evidence 2: Consequently, summers are 2.3 °C (4 °F) warmer in the Northern Hemisphere than in the Southern Hemisphere under similar conditions.
Evidence 3: "Centennial-scale climate cooling with a sudden event around 8,200 years ago".
Evidence 4: This period of warmth ended about 5,500 years ago with the descent into the Neoglacial and concomitant Neopluvial.
Evidence 5: Research using sediment in lakes near the Okstind Glacier has shown that the summer climate in Nordland was up to 2.5 °C warmer 9,000 to 6,000 years ago, and then slowly cooled—it was 0.5 °C warmer 2,000 years before present (see Holocene climatic optimum.).
Answer: NOT_ENOUGH_INFO

Claim: the world is b

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


...

Claim: This could mean the landmark Paris Climate Agreement – which seeks to limit global warming to 2 degrees Celsius (3.6 degrees Fahrenheit) above pre-industrial levels – may not be enough to ward off catastrophe.
Evidence 1: Although the parties to the UNFCCC have agreed that deep cuts in emissions are required and that global warming should be limited to well below 2 °C (3.6 °F) in the Paris Agreement of 2016, the Earth's average surface temperature has already increased by about half this threshold and current pledges by countries to cut emissions are inadequate to limit future warming.
Evidence 2: In 2015 all UN countries negotiated the Paris Agreement, which aims to keep climate change well below 2 °C.
Answer: SUPPORTS

Claim: Scientists say the recent climate agreement negotiated in Paris is not remotely ambitious enough to forestall a significant melting of Greenland and Antarctica, though if fully implemented, it may slow the pace somewhat.”
Evidence 1: Although the parties 

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Claim: The minute increase of anthropogenic CO2 in the atmosphere (0.008%) was not the cause of the warming—it was a continuation of natural cycles that occurred over the past 500 years."
Evidence 1: The introduction includes this statement: There is strong evidence that the warming of the Earth over the last half-century has been caused largely by human activity, such as the burning of fossil fuels and changes in land use, including agriculture and deforestation.
Evidence 2: Human-caused increases in greenhouse gases are responsible for most of the observed global average surface warming of roughly 0.8 °C (1.5 °F) over the past 140 years.
Answer: REFUTES

Claim: "An article in Science magazine illustrated that a rise in carbon dioxide did not precede a rise in temperatures, but actually lagged behind temperature rises by 200 to 1000 years.
Evidence 1: Studies of the Vostok ice core show that at the "beginning of the deglaciations, the CO 2 increase either was in phase or lagged by les

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Claim: Climate Models Have Overestimated Global Warming
Evidence 1: Past models have underestimated the rate of Arctic shrinkage and underestimated the rate of precipitation increase.
Evidence 2: The 2017 United States-published National Climate Assessment notes that "climate models may still be underestimating or missing relevant feedback processes".
Evidence 3: Lindzen said that predicted warming may be overestimated because of their handling of the climate system's water vapor feedback.
Answer: DISPUTED

Claim: "[Models] are full of fudge factors that are fitted to the existing climate, so the models more or less agree with the observed data.
Evidence 1: In the case of an inconsistency between the data and model's results, the general tendency is to try to make minimal modifications to the model so that it produces results that fit the data.
Evidence 2: As the purpose of modeling is to increase our understanding of the world, the validity of a model rests not only on its fit to empi

In [ ]:
df_dev_pred_1 = pd.DataFrame(predicted_1)
df_dev_pred_new_1 = df_dev.merge(df_dev_pred_1[['claim_id', 'predicted_label']], on='claim_id', how='left')
df_dev_pred_new_1['claim_label'] = df_dev_pred_new_1['predicted_label']
df_dev_pred_new_1 = df_dev_pred_new_1.drop(columns=['predicted_label'])

data_1 = {
    row["claim_id"]: {
        "claim_label": row["claim_label"],
        "evidences": row["evidences"]
    }
    for _, row in df_dev_pred_new_1.iterrows()
}

with open("dev-claims-predicted-icl-1.json", "w", encoding="utf-8") as f:
    json.dump(data_1, f, indent=2, ensure_ascii=False)

In [ ]:
!python eval.py --predictions dev-claims-predicted-icl-1.json --groundtruth dev-claims.json

Evidence Retrieval F-score (F)    = 0.16232735518449806
Claim Classification Accuracy (A) = 0.38961038961038963
Harmonic Mean of F and A          = 0.22917231044366945


#### b. Prompt 2 Testing

In [ ]:
predicted_2 = []

for _, row in df_dev_pairs.iterrows():
    pred_label_2 = icl_predict_label(
        claim_text=row['claim_text'],
        evidence_text=row['evidence_text'],
        df_train_pairs=df_train_pairs,
        train_embeddings=train_embeddings,
        tokenizer=tokenizer,
        get_prompt_fn=get_prompt2,
        num_examples=5
    )
    predicted_2.append({
        "claim_id": row['claim_id'],
        "claim_text": row['claim_text'],
        "predicted_label": pred_label_2
    })

/usr/local/lib/python3.11/dist-packages/transformers/generation/configuration_utils.py:631: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.0` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Given a claim and supporting evidence, classify the final claim into one of:SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTEDClaim: When South Australians buy electricity at $14,200/MWh, they are paying the equivalent of $400 a litre for petrol.
Evidence 1: The retail price of petrol is 75.00 Rs/litre in 2012-13.
Evidence 2: The affordable electricity retail price (860 kcal/kWh at 75% input electricity to shaft power efficiency) to replace petrol (lower heating value 7693 kcal/litre at 33% fuel energy to crank shaft efficiency) is 19.06 Rs/kWh.
Evidence 3: The kilowatt-hour (kWh, also kW⋅h or kW h) is a unit of energy equal to 3600 kilojoules (3.6 megajoules).
Evidence 4: The maximum price was $14,000/MWh in 2016-2017, $13,800/MWh in 2015-2016, $13,500/MWh in 2014-2015, and $13,100/MWh in 2013-2014.
Evidence 5: As of 2018, the unsubsidised levelised cost of electricity for utility scale solar power is around $43/MWh.
Answer: NOT_ENOUGH_INFO

Claim: Australia has more solar coverage than 

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Given a claim and supporting evidence, classify the final claim into one of:SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTEDClaim: Fifty-five thousand years ago the whole world was 2°C warmer than it is today[...]
Evidence 1: During the LGM 22,000 YBP the average summer temperature was 3–5 °C (5–9 °F) degrees cooler than today, with variations of 2.9 °C (5.2 °F) degrees cooler on the Seward Peninsula to 7.5 °C (13.5 °F) cooler in the Yukon.
Evidence 2: Consequently, summers are 2.3 °C (4 °F) warmer in the Northern Hemisphere than in the Southern Hemisphere under similar conditions.
Evidence 3: "Centennial-scale climate cooling with a sudden event around 8,200 years ago".
Evidence 4: This period of warmth ended about 5,500 years ago with the descent into the Neoglacial and concomitant Neopluvial.
Evidence 5: Research using sediment in lakes near the Okstind Glacier has shown that the summer climate in Nordland was up to 2.5 °C warmer 9,000 to 6,000 years ago, and then slowly cooled—it wa

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


...

Given a claim and supporting evidence, classify the final claim into one of:SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTEDClaim: This could mean the landmark Paris Climate Agreement – which seeks to limit global warming to 2 degrees Celsius (3.6 degrees Fahrenheit) above pre-industrial levels – may not be enough to ward off catastrophe.
Evidence 1: Although the parties to the UNFCCC have agreed that deep cuts in emissions are required and that global warming should be limited to well below 2 °C (3.6 °F) in the Paris Agreement of 2016, the Earth's average surface temperature has already increased by about half this threshold and current pledges by countries to cut emissions are inadequate to limit future warming.
Evidence 2: In 2015 all UN countries negotiated the Paris Agreement, which aims to keep climate change well below 2 °C.
Answer: SUPPORTS

Claim: Scientists say the recent climate agreement negotiated in Paris is not remotely ambitious enough to forestall a significant melting 

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Given a claim and supporting evidence, classify the final claim into one of:SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTEDClaim: The minute increase of anthropogenic CO2 in the atmosphere (0.008%) was not the cause of the warming—it was a continuation of natural cycles that occurred over the past 500 years."
Evidence 1: The introduction includes this statement: There is strong evidence that the warming of the Earth over the last half-century has been caused largely by human activity, such as the burning of fossil fuels and changes in land use, including agriculture and deforestation.
Evidence 2: Human-caused increases in greenhouse gases are responsible for most of the observed global average surface warming of roughly 0.8 °C (1.5 °F) over the past 140 years.
Answer: REFUTES

Claim: "An article in Science magazine illustrated that a rise in carbon dioxide did not precede a rise in temperatures, but actually lagged behind temperature rises by 200 to 1000 years.
Evidence 1: Studies of t

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Given a claim and supporting evidence, classify the final claim into one of:SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTEDClaim: Climate Models Have Overestimated Global Warming
Evidence 1: Past models have underestimated the rate of Arctic shrinkage and underestimated the rate of precipitation increase.
Evidence 2: The 2017 United States-published National Climate Assessment notes that "climate models may still be underestimating or missing relevant feedback processes".
Evidence 3: Lindzen said that predicted warming may be overestimated because of their handling of the climate system's water vapor feedback.
Answer: DISPUTED

Claim: "[Models] are full of fudge factors that are fitted to the existing climate, so the models more or less agree with the observed data.
Evidence 1: In the case of an inconsistency between the data and model's results, the general tendency is to try to make minimal modifications to the model so that it produces results that fit the data.
Evidence 2: As the p

In [ ]:
df_dev_pred_2 = pd.DataFrame(predicted_2)
df_dev_pred_new_2 = df_dev.merge(df_dev_pred_2[['claim_id', 'predicted_label']], on='claim_id', how='left')
df_dev_pred_new_2['claim_label'] = df_dev_pred_new_2['predicted_label']
df_dev_pred_new_2 = df_dev_pred_new_2.drop(columns=['predicted_label'])

data_2 = {
    row["claim_id"]: {
        "claim_label": row["claim_label"],
        "evidences": row["evidences"]
    }
    for _, row in df_dev_pred_new_2.iterrows()
}

with open("dev-claims-predicted-icl-2.json", "w", encoding="utf-8") as f:
    json.dump(data_2, f, indent=2, ensure_ascii=False)

In [ ]:
!python eval.py --predictions dev-claims-predicted-icl-2.json --groundtruth dev-claims.json

Evidence Retrieval F-score (F)    = 0.16232735518449806
Claim Classification Accuracy (A) = 0.44155844155844154
Harmonic Mean of F and A          = 0.23738599041130232


#### c. Prompt 3 Testing

In [ ]:
predicted_3 = []

for _, row in df_dev_pairs.iterrows():
    pred_label_3 = icl_predict_label(
        claim_text=row['claim_text'],
        evidence_text=row['evidence_text'],
        df_train_pairs=df_train_pairs,
        train_embeddings=train_embeddings,
        tokenizer=tokenizer,
        get_prompt_fn=get_prompt3,
        num_examples=5
    )
    predicted_3.append({
        "claim_id": row['claim_id'],
        "claim_text": row['claim_text'],
        "predicted_label": pred_label_3
    })

/usr/local/lib/python3.11/dist-packages/transformers/generation/configuration_utils.py:631: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.0` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Question: Is the claim supported by the evidence? Answer with one of: SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTEDClaim: When South Australians buy electricity at $14,200/MWh, they are paying the equivalent of $400 a litre for petrol.
Evidence 1: The retail price of petrol is 75.00 Rs/litre in 2012-13.
Evidence 2: The affordable electricity retail price (860 kcal/kWh at 75% input electricity to shaft power efficiency) to replace petrol (lower heating value 7693 kcal/litre at 33% fuel energy to crank shaft efficiency) is 19.06 Rs/kWh.
Evidence 3: The kilowatt-hour (kWh, also kW⋅h or kW h) is a unit of energy equal to 3600 kilojoules (3.6 megajoules).
Evidence 4: The maximum price was $14,000/MWh in 2016-2017, $13,800/MWh in 2015-2016, $13,500/MWh in 2014-2015, and $13,100/MWh in 2013-2014.
Evidence 5: As of 2018, the unsubsidised levelised cost of electricity for utility scale solar power is around $43/MWh.
Answer: NOT_ENOUGH_INFO

Claim: Australia has more solar coverage than any ot

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Question: Is the claim supported by the evidence? Answer with one of: SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTEDClaim: Fifty-five thousand years ago the whole world was 2°C warmer than it is today[...]
Evidence 1: During the LGM 22,000 YBP the average summer temperature was 3–5 °C (5–9 °F) degrees cooler than today, with variations of 2.9 °C (5.2 °F) degrees cooler on the Seward Peninsula to 7.5 °C (13.5 °F) cooler in the Yukon.
Evidence 2: Consequently, summers are 2.3 °C (4 °F) warmer in the Northern Hemisphere than in the Southern Hemisphere under similar conditions.
Evidence 3: "Centennial-scale climate cooling with a sudden event around 8,200 years ago".
Evidence 4: This period of warmth ended about 5,500 years ago with the descent into the Neoglacial and concomitant Neopluvial.
Evidence 5: Research using sediment in lakes near the Okstind Glacier has shown that the summer climate in Nordland was up to 2.5 °C warmer 9,000 to 6,000 years ago, and then slowly cooled—it was 0.5 

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


...

Question: Is the claim supported by the evidence? Answer with one of: SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTEDClaim: This could mean the landmark Paris Climate Agreement – which seeks to limit global warming to 2 degrees Celsius (3.6 degrees Fahrenheit) above pre-industrial levels – may not be enough to ward off catastrophe.
Evidence 1: Although the parties to the UNFCCC have agreed that deep cuts in emissions are required and that global warming should be limited to well below 2 °C (3.6 °F) in the Paris Agreement of 2016, the Earth's average surface temperature has already increased by about half this threshold and current pledges by countries to cut emissions are inadequate to limit future warming.
Evidence 2: In 2015 all UN countries negotiated the Paris Agreement, which aims to keep climate change well below 2 °C.
Answer: SUPPORTS

Claim: Scientists say the recent climate agreement negotiated in Paris is not remotely ambitious enough to forestall a significant melting of Gre

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Question: Is the claim supported by the evidence? Answer with one of: SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTEDClaim: The minute increase of anthropogenic CO2 in the atmosphere (0.008%) was not the cause of the warming—it was a continuation of natural cycles that occurred over the past 500 years."
Evidence 1: The introduction includes this statement: There is strong evidence that the warming of the Earth over the last half-century has been caused largely by human activity, such as the burning of fossil fuels and changes in land use, including agriculture and deforestation.
Evidence 2: Human-caused increases in greenhouse gases are responsible for most of the observed global average surface warming of roughly 0.8 °C (1.5 °F) over the past 140 years.
Answer: REFUTES

Claim: "An article in Science magazine illustrated that a rise in carbon dioxide did not precede a rise in temperatures, but actually lagged behind temperature rises by 200 to 1000 years.
Evidence 1: Studies of the Vos

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Question: Is the claim supported by the evidence? Answer with one of: SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTEDClaim: Climate Models Have Overestimated Global Warming
Evidence 1: Past models have underestimated the rate of Arctic shrinkage and underestimated the rate of precipitation increase.
Evidence 2: The 2017 United States-published National Climate Assessment notes that "climate models may still be underestimating or missing relevant feedback processes".
Evidence 3: Lindzen said that predicted warming may be overestimated because of their handling of the climate system's water vapor feedback.
Answer: DISPUTED

Claim: "[Models] are full of fudge factors that are fitted to the existing climate, so the models more or less agree with the observed data.
Evidence 1: In the case of an inconsistency between the data and model's results, the general tendency is to try to make minimal modifications to the model so that it produces results that fit the data.
Evidence 2: As the purpose

In [ ]:
df_dev_pred_3 = pd.DataFrame(predicted_3)
df_dev_pred_new_3 = df_dev.merge(df_dev_pred_3[['claim_id', 'predicted_label']], on='claim_id', how='left')
df_dev_pred_new_3['claim_label'] = df_dev_pred_new_3['predicted_label']
df_dev_pred_new_3 = df_dev_pred_new_3.drop(columns=['predicted_label'])


data_3 = {
    row["claim_id"]: {
        "claim_label": row["claim_label"],
        "evidences": row["evidences"]
    }
    for _, row in df_dev_pred_new_3.iterrows()
}


with open("dev-claims-predicted-icl-3.json", "w", encoding="utf-8") as f:
    json.dump(data_3, f, indent=2, ensure_ascii=False)

In [ ]:
!python eval.py --predictions dev-claims-predicted-icl-3.json --groundtruth dev-claims.json

Evidence Retrieval F-score (F)    = 0.16232735518449806
Claim Classification Accuracy (A) = 0.4675324675324675
Harmonic Mean of F and A          = 0.24098475940266842


### 3.2.4 Test Inference

In [ ]:
with open("test-claims-predictions-hard.json", "r", encoding="utf-8") as f:
    test_claims = json.load(f)

df_test_claims = pd.DataFrame([
    {
        "claim_id": cid,
        "claim_text": cinfo["claim_text"],
        "evidences": cinfo["evidences"]
    }
    for cid, cinfo in test_claims.items()
])

df_test_combined = build_input_pairs_combined(df_test_claims, df_evidence, keep_ids=True)

In [ ]:
prompt_methods = [
    ("get_prompt1", get_prompt1),
    ("get_prompt2", get_prompt2),
    ("get_prompt3", get_prompt3)
]

for i, (name, get_prompt_fn) in enumerate(prompt_methods, 1):

    test_predicted = []
    for _, row in df_test_combined.iterrows():
        pred_label = icl_predict_label(
            claim_text=row['claim_text'],
            evidence_text=row['evidence_text'],
            df_train_pairs=df_train_pairs,
            train_embeddings=train_embeddings,
            tokenizer=tokenizer,
            get_prompt_fn=get_prompt_fn,
            num_examples=5
        )
        test_predicted.append({
            "claim_id": row['claim_id'],
            "claim_text": row['claim_text'],
            "evidences": row['evidence_ids'],
            "claim_label": pred_label
        })


    test_result = {
        row["claim_id"]: {
            "claim_text": row["claim_text"],
            "claim_label": row["claim_label"],
            "evidences": row["evidences"]
        }
        for row in test_predicted
    }

    output_filename = f"test-output-icl-{i}.json"
    with open(output_filename, "w", encoding="utf-8") as f:
        json.dump(test_result, f, indent=2, ensure_ascii=False)

    print(f"Results saved to:{output_filename}")


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Claim: The human contribution to global warming was about 0.01°C.
Evidence 1: Human-caused increases in greenhouse gases are responsible for most of the observed global average surface warming of roughly 0.8 °C (1.5 °F) over the past 140 years.
Answer: REFUTES

Claim: The climate debate is, in reality, about a 1.6 watts per square metre or 0.5 per cent discrepancy in the poorly known planetary energy balance."
Evidence 1: There is no consensus over the magnitude of long-term carbon leakage.
Evidence 2: On average the price per square metre in central London is €24,252 (April 2014).
Evidence 3: In mathematics, a percentage (from Latin per centum "by a hundred") is a number or ratio expressed as a fraction of 100.
Evidence 4: ", as opposed to "per cent".
Evidence 5: Watts Up With That features material disputing the scientific consensus on climate change, including claims the human role in global warming is insignificant and carbon dioxide is not a driving force of warming.
Answer: NOT_E

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Claim: Overall Greenland is losing ice mass at an accelerating rate.
Evidence 1: The rate of the decline in entire Arctic ice coverage is accelerating.
Evidence 2: Average annual ice loss in Greenland more than doubled in the early 21st century compared to the 20th century.
Evidence 3: "A tipping point in refreezing accelerates mass loss of Greenland's glaciers and ice caps".
Answer: SUPPORTS

Claim: Greenland on the whole is losing ice, as confirmed by satellite measurement.
Evidence 1: These measurements came from the US space agency's GRACE (Gravity Recovery and Climate Experiment) satellite, launched in 2002, as reported by BBC.
Evidence 2: Play media Satellite measurements of Greenland's ice cover from 1979 to 2009 reveals a trend of increased melting.
Evidence 3: This glacier was discovered in 2002 to be shrinking rapidly, and by 2007 had completely melted away, leaving the exposed island.
Evidence 4: Findings show that Greenland has lost 3.8 trillion tonnes of ice since 1992, en

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


...

Question: Is the claim supported by the evidence? Answer with one of: SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTEDClaim: it’s virtually impossible to get funded for work that disputes climate change through other channels [other than oil companies]
Evidence 1: The New York Times and others reported in 2015 that oil companies knew that burning oil and gas could cause climate change and global warming since the 1970s but nonetheless funded deniers for years.
Answer: SUPPORTS

Claim: U.S. Pays $1 Billion into Green Climate Fund, Top Polluters Pay Nothing
Evidence 1: "United States delivers first payment to global climate fund".
Evidence 2: So far, the Green Climate Fund has now received over $10 billion in pledges.
Answer: DISPUTED

Claim: Climate scientists could make far more money in other careers - most notably, working for the oil industry.
Evidence 1: He has accepted more than $1.2 million in money from the fossil-fuel industry over the last decade while failing to disclose that 

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Question: Is the claim supported by the evidence? Answer with one of: SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTEDClaim: Since the beginning of the Industrial Revolution, the acidity of surface ocean waters has increased by about 30 percent.13,14
Evidence 1: This has caused an increase in hydrogen ion (acidity) of about 30% since the start of the industrial age through a process known as "ocean acidification."
Evidence 2: Ocean acidification has increased 26% since the beginning of the industrial era.
Evidence 3: Between 1751 and 1996, surface ocean pH is estimated to have decreased from approximately 8.25 to 8.14, representing an increase of almost 30% in H+ ion concentration in the world's oceans.
Answer: SUPPORTS

Claim: CO2 emissions from all commercial operations in 2018 totaled 918 million metric tons—2.4% of global CO2 emissions from fossil fuel use.
Evidence 1: In 2018, global commercial operations emitted 918 million tonnes (Mt) of CO₂, 2.4% of all CO₂ emissions: 747 Mt for

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Question: Is the claim supported by the evidence? Answer with one of: SUPPORTS / REFUTES / NOT_ENOUGH_INFO / DISPUTEDClaim: The long-term correlation between CO2 and temperature is well established.
Evidence 1: During the glacial cycles, there was a high correlation between CO 2 concentrations and temperatures.
Evidence 2: Correlation of CO 2 and temperature is not part of this evidence.
Evidence 3: "Coherence established between atmospheric carbon dioxide and global temperature".
Evidence 4: Further research has demonstrated a reliable correlation between CO 2 levels and the temperature calculated from ice isotope data.
Evidence 5: There is also a close correlation between CO2 and temperature, where CO2 has a strong control over global temperatures in Earth history.
Answer: DISPUTED

Claim: There are many lines of evidence which clearly show that the atmospheric CO2 increase is caused by humans.
Evidence 1: Human activities have caused CO 2 to increase above levels not seen in hundred